In [2]:
import json, os
import pandas as pd
from pandas.io.json import json_normalize
from bs4 import BeautifulSoup
import re 

In [3]:
path_to_json = 'howest_dataset/'
dataset= pd.DataFrame()
json_files = [pos_json for pos_json in os.listdir(path_to_json) if pos_json.endswith('.json')]

for json_file in json_files:
    json_file=path_to_json+json_file
    with open(json_file) as train_file:
        dict_train = json.load(train_file)
    file_df=pd.DataFrame.from_dict(pd.json_normalize(dict_train), orient='columns')
    dataset=dataset.append(file_df)

In [4]:
dataset.head(1000)

language client_reference  \
0     fr_BE     ZSN202006957   
0     fr_BE     ZSN202010883   
0     nl_BE     NSN202011807   
0     fr_BE   ZSN20201297601   
0     nl_BE     NSN202013139   
..      ...              ...   
0     nl_BE     NSN202005767   
0     nl_BE     NSN212000940   
0     nl_BE     NSN212001202   
0     fr_BE   NSN20102929902   
0     nl_BE       C302005548   

                                         mail_subject  \
0                 MISSION_ASSIGNEMENT: ZSN20200695701   
0                 MISSION_ASSIGNEMENT: ZSN20201088301   
0                 MISSION_ASSIGNEMENT: NSN20201180701   
0                 MISSION_ASSIGNEMENT: ZSN20201297601   
0                 MISSION_ASSIGNEMENT: NSN20201313901   
..                                                ...   
0                 MISSION_ASSIGNEMENT: NSN20200576701   
0                 MISSION_ASSIGNEMENT: NSN21200094001   
0                 MISSION_ASSIGNEMENT: NSN21200120201   
0                 MISSION_ASSIGNEMENT: NSN20102929902   
0   Betreft het schadegeval nr. *C302005548* van 3...   

                                         mail_content           party_id  \
0   <anon> annexe nous vous transmettons un docume...  21955048183443173   
0   <anon> annexe nous vous transmettons un docume...  21955048183443173   
0   in bijlage <anon> wij een document met betrekk...  21955048183443173   
0   <anon> annexe nous vous transmettons un docume...  21955048183443173   
0   in bijlage <anon> wij een document met betrekk...  21955048183443173   
..                                                ...                ...   
0   in bijlage <anon> wij een document met betrekk...  21955048183443173   
0   in bijlage <anon> wij een document met betrekk...  21955048183443173   
0   in bijlage <anon> wij een document met betrekk...  21955048183443173   
0   <anon> annexe nous vous transmettons un docume...  21955048183443173   
0   <anon> <anon> <anon> <anon> <anon> <anon> <ano...  21955048183443174   

          party_type            unit_id organization                from_mail  \
0   nonNaturalPerson               None      Allianz   NoReplyECNM@allianz.be   
0   nonNaturalPerson               None      Allianz   NoReplyECNM@allianz.be   
0   nonNaturalPerson  24206847997116432      Allianz   NoReplyECNM@allianz.be   
0   nonNaturalPerson  24206847997116432      Allianz   NoReplyECNM@allianz.be   
0   nonNaturalPerson  24206847997116432      Allianz   NoReplyECNM@allianz.be   
..               ...                ...          ...                      ...   
0   nonNaturalPerson  24206847997116432      Allianz   NoReplyECNM@allianz.be   
0   nonNaturalPerson  24206847997116432      Allianz   NoReplyECNM@allianz.be   
0   nonNaturalPerson  24206847997116432      Allianz   NoReplyECNM@allianz.be   
0   nonNaturalPerson  24206847997116432      Allianz   NoReplyECNM@allianz.be   
0   nonNaturalPerson  24206847997116443    P&V Groep  claims-BA-ANT@vivium.be   

               comments                                        attachments  \
0                        [{'filename': 'MISSION_ASSIGNEMENT.pdf', 'cont...   
0                        [{'filename': 'MISSION_ASSIGNEMENT.pdf', 'cont...   
0             Beheer     [{'filename': 'MISSION_ASSIGNEMENT.pdf', 'cont...   
0             Beheer     [{'filename': 'MISSION_ASSIGNEMENT.pdf', 'cont...   
0             Beheer     [{'filename': 'courtier envoie le devis et con...   
..                  ...                                                ...   
0             Beheer     [{'filename': 'MISSION_ASSIGNEMENT.pdf', 'cont...   
0             Beheer     [{'filename': 'MISSION_ASSIGNEMENT.pdf', 'cont...   
0             Beheer     [{'filename': 'MISSION_ASSIGNEMENT.pdf', 'cont...   
0             Beheer     [{'filename': 'MISSION_ASSIGNEMENT.pdf', 'cont...   
0   Claims BA Antwerpen  [{'filename': 'via agt  oaingebrekestelling.pd...   

   labels.assignment_type labels.case_type labels.sub_case_type  \
0              Unilateral         Property 

In [112]:
def text_processing(content):
    text_no_html = BeautifulSoup(str(content),"html.parser" ).get_text()
    text_alpha_chars = re.sub("[^a-zA-Z']", " ", str(text_no_html)) 
    text_lower = text_alpha_chars.lower()
    return text_lower

def get_fileNames(attachment):
    fileNames=[]
    for obj in attachment:
        fileNames.append(obj['filename'].replace('.pdf', ''))
        fileNamesStr = ' '.join(fileNames)
    return fileNamesStr

def get_content(attachment):
    contents=[]
    for obj in attachment:
        contents.append(obj['content'])
        contentsStr = ' '.join(contents)
        contentsStr=text_processing(contentsStr)
    return contentsStr
    
dataset['mail_content']=dataset['mail_content'].apply(text_processing)
dataset['attachments_filename']=dataset['attachments'].apply(get_fileNames)
dataset['attachments_content']=dataset['attachments'].apply(get_content)
dataset.drop('attachments', axis=1, inplace=True) 

In [115]:
pd.set_option("display.max_rows", None)
dataset.head(10000)

language client_reference  \
0    fr_BE     ZSN202006957   
0    fr_BE     ZSN202010883   
0    nl_BE     NSN202011807   
0    fr_BE   ZSN20201297601   
0    nl_BE     NSN202013139   
0    nl_BE       C202028773   
0    nl_BE       C202034750   
0    nl_BE       C302005692   
0    fr_BE   NSN21200147702   
0    nl_BE       C202027039   
0    fr_BE     ZSN192012330   
0    fr_BE     ZSN212001608   
0    nl_BE       C302006544   
0    nl_BE     NSN202012397   
0    nl_BE       C202017876   
0    nl_BE     NSN202008149   
0    nl_BE   NSN20200822501   
0    nl_BE       C882001083   
0    nl_BE     NSN206004050   
0    nl_BE       C302009598   
0    nl_BE       C302004650   
0    nl_BE       C302006682   
0    nl_BE     NSN202014886   
0    nl_BE       C202107978   
0    nl_BE       C202105945   
0    fr_BE       C302100434   
0    nl_BE       C302007569   
0    fr_BE     ZSN202009122   
0    nl_BE       C302008366   
0    fr_BE     ZSN202012294   
0    nl_BE       C202101005   
0    nl_BE       C302101858   
0    nl_BE       C302102327   
0    nl_BE     NSN202006696   
0    nl_BE   NSN21200118601   
0    nl_BE       C302103166   
0    nl_BE     NSN196005248   
0    fr_BE       C882100231   
0    nl_BE     NSN202010607   
0    fr_BE     ZSN202007307   
0    fr_BE   ZSN21200109901   
0    nl_BE   NSN20201276201   
0    nl_BE     NSN202009426   
0    nl_BE     NSN204001327   
0    nl_BE       C302005295   
0    nl_BE   NSN20201110201   
0    nl_BE     NSN202011295   
0    nl_BE       C202106797   
0    nl_BE     NSN192010609   
0    nl_BE       C302005153   
0    fr_BE       C302100199   
0    nl_BE     NSN206002096   
0    fr_BE     ZSN212001433   
0    nl_BE     ZSN202013128   
0    nl_BE       C302005850   
0    nl_BE   NSN21200255101   
0    fr_BE     ZSN202006916   
0    fr_BE     ZSN202010968   
0    nl_BE     NSN202012293   
0    nl_BE       C302102331   
0    fr_BE   ZSN19201601901   
0    fr_BE   ZSN21200071501   
0    nl_BE       C102107595   
0    nl_BE     NSN202014347   
0    nl_BE     NSN202009963   
0    fr_BE     ZSN216000498   
0    nl_BE       C302102274   
0    nl_BE       C202035946   
0    nl_BE       C302007744   
0    nl_BE       C202024204   
0    nl_BE   ZSN20201351701   
0    fr_BE     ZSN212000721   
0    fr_BE     ZSN192008005   
0    nl_BE     NSN202008558   
0    nl_BE       C302008632   
0    nl_BE       C302100160   
0    nl_BE     NSN202014081   
0    nl_BE       C202023742   
0    nl_BE       C302009023   
0    nl_BE   NSN18201519401   
0    nl_BE     NSN206001643   
0    nl_BE   NSN20201280601   
0    nl_BE       C302101264   
0    fr_BE   ZSN21200254201   
0    fr_BE   NSN21200012601   
0    nl_BE   NSN20201502501   
0    nl_BE     NSN202013251   
0    fr_BE     ZSN212002659   
0    nl_BE       C302000039   
0    nl_BE       C302007206   
0    nl_BE     NSN202009522   
0    nl_BE     NSN206003015   
0    nl_BE   NSN19201601801   
0    nl_BE       C302006417   
0    nl_BE     NSN202011954   
0    fr_BE     ZSN202012847   
0    nl_BE     NSN212000360   
0    nl_BE       C202035911   
0    fr_BE     ZSN212002198   
0    nl_BE       C302102389   
0    fr_BE   ZSN20201149401   
0    nl_BE     NSN192010074   
0    nl_BE       C302007343   
0    nl_BE     NSN202012801   
0    nl_BE       C302100567   
0    nl_BE     NSN206002192   
0    nl_BE     NSN212001658   
0    fr_BE     ZSN182015203   
0    fr_BE     ZSN216000709   
0    fr_BE   ZSN21200124101   
0    fr_BE     ZSN202014356   
0    nl_BE     NSN202012417   
0    nl_BE       C302002993   
0    nl_BE       C302004144   
0    fr_BE     ZSN212001235   
0    nl_BE     NSN202011885   
0    nl_BE       C302101927   
0    fr_BE   ZSN21200240901   
0    nl_BE     NSN206003828   
0    fr_BE     ZSN192015861   
0    fr_BE       C302101862   
0    fr_BE   ZSN20201388301   
0    fr_BE     zsn202008924   
0    nl_BE       C302100320   
0    nl_BE     NSN205500044   
0    nl_BE     NSN202013857   
0    fr_BE     ZSN212001720   
0    fr_BE   ZSN20201507101   
0  